<img style="float: right;" width="120" src="http://neueda.conygre.com/pydata/images/neueda-logo.jpeg">
<br><br><br>


This notebook will explain the following topics and concepts:


**DataFrames** 
- Rows and Columns - adding & removing
- Adding new columns to a DataFrame
- Inserting rows using values calculated from values in other rows
- Filtering Data
- Sorting Data
- Sorting Indexes
- Resetting Indexes
- Multi Indexes and Cross Sections


# Importing the libraries

Almost every piece of Data Analysis you carry out using python with begin with these 3 lines of code.

In [ ]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt

%matplotlib inline


# format for floats
pd.options.display.float_format = '{:,.2f}'.format

## Load in some data from 

- Use the **read_excel** function to read the contents of a spreadsheet into a DataFrame.


** Note **

The data we are using in this example came from a single excel file<br>
- The excel file has 3 work sheets in it containing price information for 3 companies: Google, IBM and Microsoft
- All 3 sheets contain the same type of information: daily trading and stock price information from 2010 to 2017
- Each set of data has a Date column, which we will use as our index (More on indexes later)
- For this example we have already exported each sheet from excel to its own csv file: Google.csv, IBM.csv, MSFT.csv
- We will read in each csv file separately
- Later in the course we will cover how to read directly from excel (.xlsx) files.

In [ ]:
xls_url = 'http://neueda.conygre.com/pydata/market_data.xls'

df_GOOGL = pd.read_excel(xls_url, sheet_name='GOOGL', index_col='Date', parse_dates=True)
df_IBM = pd.read_excel(xls_url, sheet_name='IBM', index_col='Date', parse_dates=True)
df_MSFT = pd.read_excel(xls_url, sheet_name='MSFT', index_col='Date', parse_dates=True)

## Selecting data

Notice in the read_csv function the parameters 
- index_col='Date' 
- parse_dates=True

**Index_col = 'Date'**<br>
- When reading in data from a csv or excel file, you can use the pandas default index or else specify which column you want as your index.
- If you use a default then the rows will be labelled numerically, starting at 0
- If you pick a column as an index, pandas will use that column as the index.
- In this case you have instructed pandas to use the 'Date' column as the index.

**parse_dates = True**
- This parameter tells pandas to translate anything in the input file that looks like a date into a date data type in the computer's memory.

Specifying  these 2 parameters in the **read_csv()** function allows you to use some quite useful selection syntax on your DataFrames

In [ ]:
from datetime import datetime

df_GOOGL['2010']
df_GOOGL['2012-03']
df_GOOGL['2012-MAR']
df_GOOGL['2013 march']

df_GOOGL['2013 march 01' : '2013 APR 01']


### Note
Dual behavior of [] in df[]

- When you don't use : inside [], then the value(s) inside it will be considered as column(s).

- When you use : inside [], then the value(s) inside it will be considered as row(s).

**Why the dual nature?**<br>
Because most of the time people want to slice the rows instead of slicing the columns. <br>
So they decided that x, y in df[x:y] should correspond to rows and x in d[x] or x, y in df[[x,y]] should correspond to column(s).


**Why does df['2017-01-02'] fails?**<br>
It will search for a column '2017-01-02', Because there is no such column, it throws an error.

**Why does df.loc['2017-01-02'] works then?**<br>
Because .loc[] has syntax of df.loc[row,column] and you can leave out the column if you will, as in your case, it simply means df.loc[row]


In [ ]:
## Crash and Burn
# df_GOOGL['2013 march 01']

# to select a singel day
df_GOOGL.loc['2013 march 01']

## Create a new DataFrame

Here you are going to create a new DataFrame called df_AdjVol.<br>
This DataFrame is going to store the **AdjVolume** for each of IBM, Microsoft and Google.<br>
- You will use the pandas DataFrame() function to create the DataFrame and then add 3 new columns to it with names 'IBM', Microsoft' and 'Google'.<br>
- You will use the data in the 'AdjVolume' columns from your previous DataFrames to populate your new DataFrame.<br>


In [ ]:
df_Vol = pd.DataFrame()

df_Vol['IBM'] = df_IBM['Volume']
df_Vol['MSoft'] = df_MSFT['Volume']
df_Vol['Google'] = df_GOOGL['Volume']

df_Vol.head()

## A 50,000 Foot view of a DataFrame

Quite often it's useful to get a quick mental image of the rows, columns, size and shape of a DataFrame.

Use the shape and size **attributes**.
- **shape** returns the number of rows and columns
- **size** returns the number of cells (rows * columns)

In addition, pandas supplies a useful **function** called **describe()** that prints out some summary information about a DataFrame.

Finally, you can use the **transpose()** function on a DataFrame to flip the output around. Transposing a DataFrame may or may not be useful depending on your personal preferences, size and shape of your data, etc.

Transposing after a **describe()** can often be useful

In [ ]:
df_Vol.shape
df_Vol.size
df_Vol.describe()
df_Vol.describe().transpose()
df_Vol.transpose()

## Filtering Data

Filters in a DataFrame allow you to conditionally select data from a DataFrame

These are very similar to filters in Excel.

syntax is 

- df[expr]

where expr is something that resolves to True or False

e.g.<br>
- All items where Volume(IBM) > 20000000


In [ ]:
# Define some constants
TWENTY_MILL = 20 * 1000 * 1000

# the filter is simply
df_Vol['IBM'] > TWENTY_MILL

# and to use the filter on a DataFrame
df_Vol [df_Vol['IBM'] > TWENTY_MILL]

Usually a good idea to name filters and to use a consistent easy to understnad naming convention

eg. lt (less than), eq (greater than) etc

e.g.<br>
- All items where Volume(IBM) > 20000000<br>
- All items where Volume(Microsoft) < 10000000
- All items where Volume(Google) > Volume(IBM)


In [ ]:
# Constants
TEN_MILL = 10 * 1000 * 1000
TWENTY_MILL = 20 * 1000 * 1000

# Filters
# Volume(IBM) > 20000000
ibm_gt_20M = df_Vol['IBM'] > TWENTY_MILL
df_Vol[ibm_gt_20M]

# Volume(Microsoft) < 10000000
msft_lt_10M = df_Vol['MSoft'] < TEN_MILL
df_Vol[msft_lt_10M]

# Volume(Google) > Volume(IBM)
goog_gt_ibm = df_Vol['Google'] > df_Vol['IBM']
df_Vol[goog_gt_ibm]

# and we can apply functions to the end of a filter
df_Vol[goog_gt_ibm].count()

# or be more selective - same filter but for the year 2017
df_Vol[goog_gt_ibm]['2017']

# Filters can be 'ANDed' together using the & symbol
# GOOGLE > IBM AND IBM >20M
df_Vol[goog_gt_ibm & ibm_gt_20M]

# Filters can be 'ORed' together using the | symbol
# GOOGLE > IBM AND MS < 10M for the year 2017
df_Vol[goog_gt_ibm | msft_lt_10M]['2017']

# Working with Rows and Columns

## Create a new DataFrame

This time, rather than loading data in from a file, you are going to create a DataFrame in place, in memory.

The code below creates a very simple DataFrame() to illustrate how to work with rows and columns.

Do not worry about the syntax, it is quite terse and concise

This DataFrame is being used to explain how to add, remove and insert rows and columns into a DataFrame.


In [ ]:
d = np.arange(16).reshape(4,4)
ndx = ['a', 'b', 'c', 'd']
cols = ['one','two','three','four']

df = pd.DataFrame(data=d, index=ndx, columns=cols)
df

## Accessing Rows and Columns

A few ways to achieve this, depends on your needs, your style, preferences, data at hand etc.

- loc gets rows or columns with particular labels from the index.
- iloc gets rows or columns at particular positions in the index (so it only takes integers).
- loc and iloc take 2 arguments - row, column
- the column argument defaults to all columns

In [ ]:
# Accessing a row with index label 'c'
df.loc['c']

# Accessing the 3rd row (index starts at 0)
df.iloc[2]

# Using loc and ioc to access columns
# Need to be a little more specific

# Accessing all rows of a column called 'three'
df.loc[:, 'three']

# Accessing all rows of the 3rd column (index starts at 0)
df.iloc[:, 2]

# Addressing individual cells
df.loc['c','three']
df.iloc[2,2]

# Accessing columns is usually achieved by specifying the column name
df['one']

# or the names of columns by using a list
df[['two','three']]
df[['three','two']]

## Removing Rows and Columns

Three choices

- drop (rows and columns)
- del (columns only)
- pop (columns only)

In [ ]:
# Removing a row
df.drop('b')

# Note that dropping returns a new DataFrame, the original is still unchanged
df

# drop returns the updated DataFrame
# often then case that we 'catch' this in another variable, leaving the original unchanged
x = df.drop('b')
x

# Can also drop multiple rows
x = df.drop(['b','c'])
x

# Can use drop to remove a column
# Use the axis parameter to specify we are referring to columns
x = df.drop('two', axis=1)
x

# or more descriptively
x = df.drop('two', axis='columns')
x

# Usually drop is for rows and pop is for columns
# pop WILL remove a column from the DataFrame
# pop returns the column removed 
# often a good idea to catch the removed column in a new variable 
x = df.pop('two')
x

df

# del deletes a column and returns nothing
# very unforgiving

del df['three']

df


## Appending Columns


- very easy to accomplish
- E.g. To add a column populated with **data** to the end of your DataFrame
  - df['NAME OF COLUMN'] = **data**
- if the column already exists, it will overwrite the values in the existing column

In [ ]:
# Add a new colum of 5's 
# This will append a new column to the DataFrame
df['five'] = 5

# Add another column which is column 'one' multiplied by column 'four'
df['six'] = df['one'] * df['four']

df

## Inserting Columns

Insert a column into the Google DataFrame between the 'Close' column and the 'Volume' column.

Call this column 'High-Low Spread'

Populate it with the difference between 'High' and 'Low'.

**NOTE**

Trying to insert a column that already exists will result in an error.

If you need to, use drop, pop or del to remove a column before re-inserting it.

In [ ]:
# Specify the location where you want the column to exist after insertion
# Sequence numbers start at 0, i.e. loc=4 inserts as the 5th column

# Before the insertion
df_GOOGL.head()

# Insert and populate
df_GOOGL.insert(loc=4, column='High-Low Spread', value=df_GOOGL['High'] - df_GOOGL['Low'])

# After insertion
df_GOOGL.head()

# Sorting Values

- Use **sort_values**
- Leaves the original unchanged and returns the updated to be caught in a new variable
- Can sort by multiple columns

In [ ]:
# Load in the SP500 Constituents and display
df_SPX = pd.read_excel(io='http://neueda.conygre.com/pydata/sample_data.xls', sheet_name='SP500', index_col='Symbol')

# Display the unsorted data
df_SPX.head(20)


# Sort by Name
df_SPX.sort_values(by='Name')


# Sort by Name - Descending
df_SPX.sort_values(by='Name', ascending=False)


# Sort by Sector then by Name
df_SPX.sort_values(by=['Sector','Name'])


# Sometimes multiple columns are stored in a local variable
cols = ['Sector', 'Name']
df_SPX.sort_values(by=cols)

# Sort by Sector Ascending and Price Descending
cols = ['Sector', 'Price']
directioNs = [True, False]
df_SPX.sort_values(by=cols, ascending=directioNs)

# Indexes

Indexes are used to 'lookup' rows or columns based on a key.

DataFrames have indexes on rows and on columns.

For our SP500 Data Set<br>
- the column index is Name, Sector, Price .....
- the row index is MMM, AOS, ABT ....

**Note** 
- neither index is sorted, they don't need to be.
- indexes do not have to be unique, although, more often than not, they are

Having Indexes on a DataFrame allows you to
- select a column df['Sector']
- select a row df.loc['FB']

You can drop an index and re-create it using a different set of values.

# Sorting Indexes

- Different use cases will require data to be sorted differently
- This Includes indexes (row indexes and column indexes)
- The default for a DataFrame is to have indexes sorted in ascending order
- Use sort_index()
- This leaves the original DataFrame unchanged and returns you the new DataFrame that you should catch in a new variable

**Note**
- Some functions can be applied to either rows or columns
- A parameter called 'axis' is passed to indicate which you want to operate on (either rows or columns)
- You can set 'axis' using the word 'rows' or 'columns' (axis='rows' OR axis='columns')
- Alternatively you can use a number: for rows axis=0, for columns axis=1


In [ ]:
# sort index will default to sorting the row index
df_SPX.sort_index()

# Sort descending
df_SPX.sort_index(ascending = False)


# You can specify sorting the the column index
# Assing either 1 or 'columns' to the axis parameter
df_SPX.sort_index(axis = 1)

df_SPX.sort_index(axis = 'columns', ascending = False)

# Sometimes useful to sort columns afgter a transpose
df_SPX.transpose().sort_index(axis=1, ascending=True)


# Same as previous buyt with a sort of the rows thrown in at the end
df_SPX.transpose().sort_index(axis=1, ascending=True).sort_index()


# Resetting Indexes

We often want to reset an index so that it becomes numerical starting at 0

We can also set a column to be the index

In [ ]:
# Reset to default 0,1...n index
df_SPX = df_SPX.reset_index()

df_SPX.head()

In [ ]:
# Set the index to the 'Name' column


df_SPX.head()

## Creating a multi-index from a file

The data in question is in the Protfolios worksheet in the sample_data spreadhseet

You are going to create a DataFrame using this file and then create a multi-level index of Rep, then Portfolio and finally Sector.

### Step 1 - Create a DataFrame from the portfolio csv file

Note that this will create a DataFrame with a default index - starting at 0 and going up in steps of 1.

In [ ]:
# First read in the file
df = pd.read_excel(io='http://neueda.conygre.com/pydata/sample_data.xls', sheet_name='Portfolios')

# Just to check that all is in order
# You could also try describe(), count, etc.
df.head()

### Step 2 - Create a MultiIndex from the Portfolio and Sector columns.

- zip - is a python function that creates a python structure called a tuple
- list creates a list
- combining them gives us a list of tuples

Once created, display the tuples to visualize what you have created

In [ ]:
# Now zip up the Portfolio and Sector columns
tuples = list(zip(df['Rep'], df['Portfolio'],df['Sector']))

hier_index = pd.MultiIndex.from_tuples(tuples)        

tuples

### Step 3 - Drop the existing index and recreate it using the multi index


In [ ]:
# Finally drop the existing index and assign a MultiIndex to the DataFrame
df.index = hier_index

df.head()

### Step 4 - Drop the unwanted columns and rename the indexes

Notice that the Portfolio and Sector columns are both present and also part of the index.

These two columns can be removed.

In [ ]:
df.pop('Portfolio')
df.pop('Sector')
df.pop('Rep')

df.index.names = ['Rep', 'Portfolio','Sector']

df.head()

### Step 5 - Cross Section the data


In [ ]:
# All Portfolios where John os the Rep
df.xs(key='John', level=0)

# Same as above
df.xs(key='John', level='Rep')

# Get all items in Portfolio P5
df.xs(key='P5', level='Portfolio')

# Get all items in 'Industrials' 
df.xs(key='Industrials',level='Sector')

# Get all items for Ringo, Portfolio 2, and Energy
df.xs(key=['Ringo', 'P2', 'Energy'], level=['Rep', 'Portfolio', 'Sector'])

# Same as above except using some variables
keys = ['Ringo', 'P2', 'Energy']
levels = ['Rep', 'Portfolio', 'Sector']
df.xs(key=keys, level=levels)